[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/kamalkraj/minGPT-TF/blob/master/play_math.ipynb)

In [56]:
#This is a 3 digs example and use all gpu with 100 iterations

In [57]:
! pip install fastprogress==0.2.3

--- Logging error ---
Traceback (most recent call last):
  File "/usr/local/lib/python3.8/dist-packages/pip/_internal/utils/logging.py", line 177, in emit
    self.console.print(renderable, overflow="ignore", crop=False, style=style)
  File "/usr/local/lib/python3.8/dist-packages/pip/_vendor/rich/console.py", line 1673, in print
    extend(render(renderable, render_options))
  File "/usr/local/lib/python3.8/dist-packages/pip/_vendor/rich/console.py", line 1305, in render
    for render_output in iter_render:
  File "/usr/local/lib/python3.8/dist-packages/pip/_internal/utils/logging.py", line 134, in __rich_console__
    for line in lines:
  File "/usr/local/lib/python3.8/dist-packages/pip/_vendor/rich/segment.py", line 249, in split_lines
    for segment in segments:
  File "/usr/local/lib/python3.8/dist-packages/pip/_vendor/rich/console.py", line 1283, in render
    renderable = rich_cast(renderable)
  File "/usr/local/lib/python3.8/dist-packages/pip/_vendor/rich/protocol.py", line 36

In [58]:
import math
import numpy as np
import tensorflow as tf
from mingpt.model import GPT, GPTConfig

In [59]:
# make deterministic
from mingpt.utils import set_seed
set_seed(42)

In [60]:
class AdditionDataset():
    """
    Returns addition problems of up to some number of digits in the inputs. Recall
    that all GPT cares about are sequences of integers, and completing them according to
    patterns in the data. Therefore, we have to somehow encode addition problems
    as a sequence of integers.
    
    The sum of two n-digit numbers gives a third up to (n+1)-digit number. So our
    encoding will simply be the n-digit first number, n-digit second number, 
    and (n+1)-digit result, all simply concatenated together. Because each addition
    problem is so structured, there is no need to bother the model with encoding
    +, =, or other tokens. Each possible sequence has the same length, and simply
    contains the raw digits of the addition problem.
    
    As a few examples, the 2-digit problems:
    - 85 + 50 = 135 becomes the sequence [8, 5, 5, 0, 1, 3, 5]
    - 6 + 39 = 45 becomes the sequence [0, 6, 3, 9, 0, 4, 5]
    etc.
    
    We will also only train GPT on the final (n+1)-digits because the first
    two n-digits are always assumed to be given. So when we give GPT an exam later,
    we will e.g. feed it the sequence [0, 6, 3, 9], which encodes that we'd like
    to add 6 + 39, and hope that the model completes the integer sequence with [0, 4, 5]
    in 3 sequential steps.
    
    fun exercise: does it help if the result is asked to be produced in reverse order?
    """

    def __init__(self, ndigit, split):
        self.split = split # train/test
        self.ndigit = ndigit
        self.vocab_size = 10 # 10 possible digits 0..9
        # +1 due to potential carry overflow, but then -1 because very last digit doesn't plug back
        self.block_size = ndigit + ndigit + ndigit + 1 - 1
        
        # split up all addition problems into either training data or test data
        num = (10**self.ndigit)**2 # total number of possible combinations
        r = np.random.RandomState(1337) # make deterministic
        perm = r.permutation(num)
        num_test = min(int(num*0.2), 1000) # 20% of the whole dataset, or only up to 1000
        self.ixes = perm[:num_test] if split == 'test' else perm[num_test:]

    def __len__(self):
        return self.ixes.size

    def __iter__(self):
        # given a problem index idx, first recover the associated a + b
        #Save the train and test data to file
        #fileName = './dataset/train_set_math_3dig.txt' if self.split == 'test' else './dataset/test_set_math_3dig.txt'
        #file = open(fileName, 'a')
        
        for idx in range(self.__len__()):
            idx = self.ixes[idx]
            nd = 10**self.ndigit
            a = idx // nd
            b = idx %  nd
            c = a + b
            print('idx='+str(idx) +' nd= ' + str(nd) + ' a=' + str(a) + ' b=' +str(b) + ' c=' +str(c))
            #idx=9927 nd= 100 a=99 b=27 c=126
            render = f'%0{self.ndigit}d%0{self.ndigit}d%0{self.ndigit+1}d' % (a,b,c) # e.g. 03+25=28 becomes "0325028"    
            print('render= ' + render)
            #render= 9927126
            #write the dataset to file
            #file.write(render+'\n')
            
            dix = [int(s) for s in render] # convert each character to its token index
            print('dix= ' + str(dix))
            #dix= [9, 9, 2, 7, 1, 2, 6]
            
            # x will be input to GPT and y will be the associated expected outputs
            x = dix[:-1]
            print('x = ' + str(x))
            #x = [9, 9, 2, 7, 1, 2]
            
            y = dix[1:] # predict the next token in the sequence
            print('y = ' + str(y))
            #y = [9, 2, 7, 1, 2, 6]
            
            y[:self.ndigit*2-1] = [-1] * (self.ndigit*2-1) # we will only train in the output locations. -100 will mask loss to zero
            print('y = ' + str(y))
            #y = [-1, -1, -1, 1, 2, 6]
            
            x = tf.convert_to_tensor(x,dtype=tf.int32)
            y = tf.convert_to_tensor(y,dtype=tf.int32)
            print('tf x = ' + str(x))
            print('tf y = ' + str(y))
            #tf x = tf.Tensor([9 9 2 7 1 2], shape=(6,), dtype=int32)
            #tf y = tf.Tensor([-1 -1 -1  1  2  6], shape=(6,), dtype=int32)
            
            yield x, y
            
        #file.close()    
    __call__ = __iter__

In [61]:
# create a dataset for e.g. 2-digit addition
ndigit = 2
train_dataset_gen = AdditionDataset(ndigit=ndigit, split='train')
test_dataset_gen = AdditionDataset(ndigit=ndigit, split='test')

In [62]:
train_dataset = tf.data.Dataset.from_generator(train_dataset_gen,(tf.int32,tf.int32))
test_dataset = tf.data.Dataset.from_generator(test_dataset_gen,(tf.int32,tf.int32))

In [63]:
# initialize a baby GPT model
mconf = GPTConfig(train_dataset_gen.vocab_size, train_dataset_gen.block_size, 
                  n_layer=2, n_head=4, n_embd=128)
# model = GPT(mconf)

In [64]:
from mingpt.trainer import Trainer, TrainerConfig

# initialize a trainer instance and kick off training
tconf = TrainerConfig(max_epochs=1, batch_size=16, learning_rate=6e-4,
                      lr_decay=True, warmup_tokens=1024, final_tokens=50*len(train_dataset_gen)*(ndigit+1),
                      num_workers=4)
trainer = Trainer(GPT, mconf, train_dataset, len(train_dataset_gen), test_dataset, len(test_dataset_gen), tconf, device='GPU:1')

config.vocab_size=10,config.n_embd=128
config.block_size=6,config.n_embd=128
config.embd_pdrop=0.33
config.n_embd=128,config.n_head=4,config.attn_pdrop=0.33,config.resid_pdrop=0.33,config.n_layer=2
EncoderLayer d_model=128,num_heads=4
EncoderLayer d_model=128,num_heads=4


In [65]:
trainer.train()

idx=4717 nd= 100 a=47 b=17 c=64
render= 4717064
dix= [4, 7, 1, 7, 0, 6, 4]
x = [4, 7, 1, 7, 0, 6]
y = [7, 1, 7, 0, 6, 4]
y = [-1, -1, -1, 0, 6, 4]
tf x = tf.Tensor([4 7 1 7 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  4], shape=(6,), dtype=int32)
idx=3455 nd= 100 a=34 b=55 c=89
render= 3455089
dix= [3, 4, 5, 5, 0, 8, 9]
x = [3, 4, 5, 5, 0, 8]
y = [4, 5, 5, 0, 8, 9]
y = [-1, -1, -1, 0, 8, 9]
tf x = tf.Tensor([3 4 5 5 0 8], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  8  9], shape=(6,), dtype=int32)
idx=1827 nd= 100 a=18 b=27 c=45
render= 1827045
dix= [1, 8, 2, 7, 0, 4, 5]
x = [1, 8, 2, 7, 0, 4]
y = [8, 2, 7, 0, 4, 5]
y = [-1, -1, -1, 0, 4, 5]
tf x = tf.Tensor([1 8 2 7 0 4], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  4  5], shape=(6,), dtype=int32)
idx=9201 nd= 100 a=92 b=1 c=93
render= 9201093
dix= [9, 2, 0, 1, 0, 9, 3]
x = [9, 2, 0, 1, 0, 9]
y = [2, 0, 1, 0, 9, 3]
y = [-1, -1, -1, 0, 9, 3]
tf x = tf.Tensor([9 2 0 1 0 9], shape=(6,), dtype=int

idx=4558 nd= 100 a=45 b=58 c=103
render= 4558103
dix= [4, 5, 5, 8, 1, 0, 3]
x = [4, 5, 5, 8, 1, 0]
y = [5, 5, 8, 1, 0, 3]
y = [-1, -1, -1, 1, 0, 3]
tf x = tf.Tensor([4 5 5 8 1 0], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  0  3], shape=(6,), dtype=int32)
idx=307 nd= 100 a=3 b=7 c=10
render= 0307010
dix= [0, 3, 0, 7, 0, 1, 0]
x = [0, 3, 0, 7, 0, 1]
y = [3, 0, 7, 0, 1, 0]
y = [-1, -1, -1, 0, 1, 0]
tf x = tf.Tensor([0 3 0 7 0 1], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  1  0], shape=(6,), dtype=int32)
idx=491 nd= 100 a=4 b=91 c=95
render= 0491095
dix= [0, 4, 9, 1, 0, 9, 5]
x = [0, 4, 9, 1, 0, 9]
y = [4, 9, 1, 0, 9, 5]
y = [-1, -1, -1, 0, 9, 5]
tf x = tf.Tensor([0 4 9 1 0 9], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  9  5], shape=(6,), dtype=int32)
idx=1576 nd= 100 a=15 b=76 c=91
render= 1576091
dix= [1, 5, 7, 6, 0, 9, 1]
x = [1, 5, 7, 6, 0, 9]
y = [5, 7, 6, 0, 9, 1]
y = [-1, -1, -1, 0, 9, 1]
tf x = tf.Tensor([1 5 7 6 0 9], shape=(6,), dtype=int32)

idx=783 nd= 100 a=7 b=83 c=90
render= 0783090
dix= [0, 7, 8, 3, 0, 9, 0]
x = [0, 7, 8, 3, 0, 9]
y = [7, 8, 3, 0, 9, 0]
y = [-1, -1, -1, 0, 9, 0]
tf x = tf.Tensor([0 7 8 3 0 9], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  9  0], shape=(6,), dtype=int32)
idx=6173 nd= 100 a=61 b=73 c=134
render= 6173134
dix= [6, 1, 7, 3, 1, 3, 4]
x = [6, 1, 7, 3, 1, 3]
y = [1, 7, 3, 1, 3, 4]
y = [-1, -1, -1, 1, 3, 4]
tf x = tf.Tensor([6 1 7 3 1 3], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  3  4], shape=(6,), dtype=int32)
idx=9780 nd= 100 a=97 b=80 c=177
render= 9780177
dix= [9, 7, 8, 0, 1, 7, 7]
x = [9, 7, 8, 0, 1, 7]
y = [7, 8, 0, 1, 7, 7]
y = [-1, -1, -1, 1, 7, 7]
tf x = tf.Tensor([9 7 8 0 1 7], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  7  7], shape=(6,), dtype=int32)
idx=6862 nd= 100 a=68 b=62 c=130
render= 6862130
dix= [6, 8, 6, 2, 1, 3, 0]
x = [6, 8, 6, 2, 1, 3]
y = [8, 6, 2, 1, 3, 0]
y = [-1, -1, -1, 1, 3, 0]
tf x = tf.Tensor([6 8 6 2 1 3], shape=(6,), dtype=i

idx=5110 nd= 100 a=51 b=10 c=61
render= 5110061
dix= [5, 1, 1, 0, 0, 6, 1]
x = [5, 1, 1, 0, 0, 6]
y = [1, 1, 0, 0, 6, 1]
y = [-1, -1, -1, 0, 6, 1]
tf x = tf.Tensor([5 1 1 0 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  1], shape=(6,), dtype=int32)
idx=2576 nd= 100 a=25 b=76 c=101
render= 2576101
dix= [2, 5, 7, 6, 1, 0, 1]
x = [2, 5, 7, 6, 1, 0]
y = [5, 7, 6, 1, 0, 1]
y = [-1, -1, -1, 1, 0, 1]
tf x = tf.Tensor([2 5 7 6 1 0], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  0  1], shape=(6,), dtype=int32)
idx=6207 nd= 100 a=62 b=7 c=69
render= 6207069
dix= [6, 2, 0, 7, 0, 6, 9]
x = [6, 2, 0, 7, 0, 6]
y = [2, 0, 7, 0, 6, 9]
y = [-1, -1, -1, 0, 6, 9]
tf x = tf.Tensor([6 2 0 7 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  9], shape=(6,), dtype=int32)
idx=4412 nd= 100 a=44 b=12 c=56
render= 4412056
dix= [4, 4, 1, 2, 0, 5, 6]
x = [4, 4, 1, 2, 0, 5]
y = [4, 1, 2, 0, 5, 6]
y = [-1, -1, -1, 0, 5, 6]
tf x = tf.Tensor([4 4 1 2 0 5], shape=(6,), dtype=in

idx=137 nd= 100 a=1 b=37 c=38
render= 0137038
dix= [0, 1, 3, 7, 0, 3, 8]
x = [0, 1, 3, 7, 0, 3]
y = [1, 3, 7, 0, 3, 8]
y = [-1, -1, -1, 0, 3, 8]
tf x = tf.Tensor([0 1 3 7 0 3], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  3  8], shape=(6,), dtype=int32)
idx=2142 nd= 100 a=21 b=42 c=63
render= 2142063
dix= [2, 1, 4, 2, 0, 6, 3]
x = [2, 1, 4, 2, 0, 6]
y = [1, 4, 2, 0, 6, 3]
y = [-1, -1, -1, 0, 6, 3]
tf x = tf.Tensor([2 1 4 2 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  3], shape=(6,), dtype=int32)
idx=9368 nd= 100 a=93 b=68 c=161
render= 9368161
dix= [9, 3, 6, 8, 1, 6, 1]
x = [9, 3, 6, 8, 1, 6]
y = [3, 6, 8, 1, 6, 1]
y = [-1, -1, -1, 1, 6, 1]
tf x = tf.Tensor([9 3 6 8 1 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  6  1], shape=(6,), dtype=int32)
idx=1850 nd= 100 a=18 b=50 c=68
render= 1850068
dix= [1, 8, 5, 0, 0, 6, 8]
x = [1, 8, 5, 0, 0, 6]
y = [8, 5, 0, 0, 6, 8]
y = [-1, -1, -1, 0, 6, 8]
tf x = tf.Tensor([1 8 5 0 0 6], shape=(6,), dtype=int

...

idx=1541 nd= 100 a=15 b=41 c=56
render= 1541056
dix= [1, 5, 4, 1, 0, 5, 6]
x = [1, 5, 4, 1, 0, 5]
y = [5, 4, 1, 0, 5, 6]
y = [-1, -1, -1, 0, 5, 6]
tf x = tf.Tensor([1 5 4 1 0 5], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  5  6], shape=(6,), dtype=int32)
idx=6001 nd= 100 a=60 b=1 c=61
render= 6001061
dix= [6, 0, 0, 1, 0, 6, 1]
x = [6, 0, 0, 1, 0, 6]
y = [0, 0, 1, 0, 6, 1]
y = [-1, -1, -1, 0, 6, 1]
tf x = tf.Tensor([6 0 0 1 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  1], shape=(6,), dtype=int32)
idx=1502 nd= 100 a=15 b=2 c=17
render= 1502017
dix= [1, 5, 0, 2, 0, 1, 7]
x = [1, 5, 0, 2, 0, 1]
y = [5, 0, 2, 0, 1, 7]
y = [-1, -1, -1, 0, 1, 7]
tf x = tf.Tensor([1 5 0 2 0 1], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  1  7], shape=(6,), dtype=int32)
idx=3985 nd= 100 a=39 b=85 c=124
render= 3985124
dix= [3, 9, 8, 5, 1, 2, 4]
x = [3, 9, 8, 5, 1, 2]
y = [9, 8, 5, 1, 2, 4]
y = [-1, -1, -1, 1, 2, 4]
tf x = tf.Tensor([3 9 8 5 1 2], shape=(6,), dtype=int

idx=3936 nd= 100 a=39 b=36 c=75
render= 3936075
dix= [3, 9, 3, 6, 0, 7, 5]
x = [3, 9, 3, 6, 0, 7]
y = [9, 3, 6, 0, 7, 5]
y = [-1, -1, -1, 0, 7, 5]
tf x = tf.Tensor([3 9 3 6 0 7], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  7  5], shape=(6,), dtype=int32)
idx=919 nd= 100 a=9 b=19 c=28
render= 0919028
dix= [0, 9, 1, 9, 0, 2, 8]
x = [0, 9, 1, 9, 0, 2]
y = [9, 1, 9, 0, 2, 8]
y = [-1, -1, -1, 0, 2, 8]
tf x = tf.Tensor([0 9 1 9 0 2], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  2  8], shape=(6,), dtype=int32)
idx=1760 nd= 100 a=17 b=60 c=77
render= 1760077
dix= [1, 7, 6, 0, 0, 7, 7]
x = [1, 7, 6, 0, 0, 7]
y = [7, 6, 0, 0, 7, 7]
y = [-1, -1, -1, 0, 7, 7]
tf x = tf.Tensor([1 7 6 0 0 7], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  7  7], shape=(6,), dtype=int32)
idx=4582 nd= 100 a=45 b=82 c=127
render= 4582127
dix= [4, 5, 8, 2, 1, 2, 7]
x = [4, 5, 8, 2, 1, 2]
y = [5, 8, 2, 1, 2, 7]
y = [-1, -1, -1, 1, 2, 7]
tf x = tf.Tensor([4 5 8 2 1 2], shape=(6,), dtype=int

idx=8563 nd= 100 a=85 b=63 c=148
render= 8563148
dix= [8, 5, 6, 3, 1, 4, 8]
x = [8, 5, 6, 3, 1, 4]
y = [5, 6, 3, 1, 4, 8]
y = [-1, -1, -1, 1, 4, 8]
tf x = tf.Tensor([8 5 6 3 1 4], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  4  8], shape=(6,), dtype=int32)
idx=8903 nd= 100 a=89 b=3 c=92
render= 8903092
dix= [8, 9, 0, 3, 0, 9, 2]
x = [8, 9, 0, 3, 0, 9]
y = [9, 0, 3, 0, 9, 2]
y = [-1, -1, -1, 0, 9, 2]
tf x = tf.Tensor([8 9 0 3 0 9], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  9  2], shape=(6,), dtype=int32)
idx=8721 nd= 100 a=87 b=21 c=108
render= 8721108
dix= [8, 7, 2, 1, 1, 0, 8]
x = [8, 7, 2, 1, 1, 0]
y = [7, 2, 1, 1, 0, 8]
y = [-1, -1, -1, 1, 0, 8]
tf x = tf.Tensor([8 7 2 1 1 0], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  0  8], shape=(6,), dtype=int32)
idx=3471 nd= 100 a=34 b=71 c=105
render= 3471105
dix= [3, 4, 7, 1, 1, 0, 5]
x = [3, 4, 7, 1, 1, 0]
y = [4, 7, 1, 1, 0, 5]
y = [-1, -1, -1, 1, 0, 5]
tf x = tf.Tensor([3 4 7 1 1 0], shape=(6,), dtype=

x = [3, 9, 2, 5, 0, 6]
y = [9, 2, 5, 0, 6, 4]
y = [-1, -1, -1, 0, 6, 4]
tf x = tf.Tensor([3 9 2 5 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  4], shape=(6,), dtype=int32)
idx=7440 nd= 100 a=74 b=40 c=114
render= 7440114
dix= [7, 4, 4, 0, 1, 1, 4]
x = [7, 4, 4, 0, 1, 1]
y = [4, 4, 0, 1, 1, 4]
y = [-1, -1, -1, 1, 1, 4]
tf x = tf.Tensor([7 4 4 0 1 1], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  1  4], shape=(6,), dtype=int32)
idx=3889 nd= 100 a=38 b=89 c=127
render= 3889127
dix= [3, 8, 8, 9, 1, 2, 7]
x = [3, 8, 8, 9, 1, 2]
y = [8, 8, 9, 1, 2, 7]
y = [-1, -1, -1, 1, 2, 7]
tf x = tf.Tensor([3 8 8 9 1 2], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  2  7], shape=(6,), dtype=int32)
idx=1164 nd= 100 a=11 b=64 c=75
render= 1164075
dix= [1, 1, 6, 4, 0, 7, 5]
x = [1, 1, 6, 4, 0, 7]
y = [1, 6, 4, 0, 7, 5]
y = [-1, -1, -1, 0, 7, 5]
tf x = tf.Tensor([1 1 6 4 0 7], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  7  5], shape=(6,), dtype=int32)
idx=8

idx=6142 nd= 100 a=61 b=42 c=103
render= 6142103
dix= [6, 1, 4, 2, 1, 0, 3]
x = [6, 1, 4, 2, 1, 0]
y = [1, 4, 2, 1, 0, 3]
y = [-1, -1, -1, 1, 0, 3]
tf x = tf.Tensor([6 1 4 2 1 0], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  0  3], shape=(6,), dtype=int32)
idx=3900 nd= 100 a=39 b=0 c=39
render= 3900039
dix= [3, 9, 0, 0, 0, 3, 9]
x = [3, 9, 0, 0, 0, 3]
y = [9, 0, 0, 0, 3, 9]
y = [-1, -1, -1, 0, 3, 9]
tf x = tf.Tensor([3 9 0 0 0 3], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  3  9], shape=(6,), dtype=int32)
idx=3613 nd= 100 a=36 b=13 c=49
render= 3613049
dix= [3, 6, 1, 3, 0, 4, 9]
x = [3, 6, 1, 3, 0, 4]
y = [6, 1, 3, 0, 4, 9]
y = [-1, -1, -1, 0, 4, 9]
tf x = tf.Tensor([3 6 1 3 0 4], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  4  9], shape=(6,), dtype=int32)
idx=8917 nd= 100 a=89 b=17 c=106
render= 8917106
dix= [8, 9, 1, 7, 1, 0, 6]
x = [8, 9, 1, 7, 1, 0]
y = [9, 1, 7, 1, 0, 6]
y = [-1, -1, -1, 1, 0, 6]
tf x = tf.Tensor([8 9 1 7 1 0], shape=(6,), dtype=i

In [66]:
trainer.display_model()

Model: "gpt_4"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_4 (Embedding)     multiple                  1280      
                                                                 
 dropout_28 (Dropout)        multiple                  0         
                                                                 
 encoder_layer_8 (EncoderLay  multiple                 198272    
 er)                                                             
                                                                 
 encoder_layer_9 (EncoderLay  multiple                 198272    
 er)                                                             
                                                                 
 layer_normalization_24 (Lay  multiple                 256       
 erNormalization)                                                
                                                             

In [67]:
from mingpt.utils import sample

In [77]:
def give_exam(dataset, batch_size=32, max_batches=-1, printResult=False):
    
    results = []
    
    loader = dataset.batch(batch_size)
    for b, (x, y) in enumerate(loader):
        print('b='+str(b))
        print('x='+str(x))
        print('y='+str(y))
        #b=0
        #x=tf.Tensor([[9 9 2 7 1 2]], shape=(1, 6), dtype=int32)
        #y=tf.Tensor([[-1 -1 -1  1  2  6]], shape=(1, 6), dtype=int32)

        d1d2 = x[:, :ndigit*2]
        print('d1d2=' +str(d1d2))
        #d1d2=tf.Tensor([[9 9 2 7]], shape=(1, 4), dtype=int32)

        d1d2d3 = sample(trainer.model, d1d2, ndigit+1)
        print('d1d2d3=' +str(d1d2d3))
        #d1d2d3=tf.Tensor([[9 9 2 7 1 1 1]], shape=(1, 7), dtype=int32)

        d3 = d1d2d3[:, -(ndigit+1):]
        print('d3=' +str(d3))
        #d3=tf.Tensor([[1 1 1]], shape=(1, 3), dtype=int32)

        factors = tf.convert_to_tensor([[10**i for i in range(ndigit+1)][::-1]])
        print('factors=' +str(factors))
        #factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
        
        # decode the integers from individual digits
        d1i = tf.reduce_sum((d1d2[:,:ndigit] * factors[:,1:]),axis=1)
        print('d1i='+str(d1i))
        #d1i=tf.Tensor([99], shape=(1,), dtype=int32)

        d2i = tf.reduce_sum((d1d2[:,ndigit:ndigit*2] * factors[:,1:]),axis=1)
        print('d2i='+str(d2i))
        #d2i=tf.Tensor([27], shape=(1,), dtype=int32)
        
        d3i_pred = tf.reduce_sum((d3 * factors),axis=1)
        print('d3i_pred='+str(d3i_pred))
        #d3i_pred=tf.Tensor([111], shape=(1,), dtype=int32)
        
        d3i_gt = d1i + d2i
        correct = (d3i_pred == d3i_gt) # Software 1.0 vs. Software 2.0 fight RIGHT on this line, lol
        for i in range(x.shape[0]):
            results.append(int(correct[i]))
            judge = 'YEP!!!' if correct[i] else 'NOPE'
            if not correct[i]:
                print("GPT claims that %03d + %03d = %03d (gt is %03d; %s)========" 
                      % (d1i[i], d2i[i], d3i_pred[i], d3i_gt[i], judge))
            elif printResult:
                print("GPT claims that %03d + %03d = %03d (gt is %03d; %s)" 
                      % (d1i[i], d2i[i], d3i_pred[i], d3i_gt[i], judge))                
        
        if max_batches >= 0 and b+1 >= max_batches:
            break

    print("final score: %d/%d = %.2f%% correct" % (np.sum(results), len(results), 100*np.mean(results)))

In [69]:
give_exam(train_dataset,batch_size=128,max_batches=-1,printResult=False)

idx=4717 nd= 100 a=47 b=17 c=64
render= 4717064
dix= [4, 7, 1, 7, 0, 6, 4]
x = [4, 7, 1, 7, 0, 6]
y = [7, 1, 7, 0, 6, 4]
y = [-1, -1, -1, 0, 6, 4]
tf x = tf.Tensor([4 7 1 7 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  4], shape=(6,), dtype=int32)
idx=3455 nd= 100 a=34 b=55 c=89
render= 3455089
dix= [3, 4, 5, 5, 0, 8, 9]
x = [3, 4, 5, 5, 0, 8]
y = [4, 5, 5, 0, 8, 9]
y = [-1, -1, -1, 0, 8, 9]
tf x = tf.Tensor([3 4 5 5 0 8], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  8  9], shape=(6,), dtype=int32)
idx=1827 nd= 100 a=18 b=27 c=45
render= 1827045
dix= [1, 8, 2, 7, 0, 4, 5]
x = [1, 8, 2, 7, 0, 4]
y = [8, 2, 7, 0, 4, 5]
y = [-1, -1, -1, 0, 4, 5]
tf x = tf.Tensor([1 8 2 7 0 4], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  4  5], shape=(6,), dtype=int32)
idx=9201 nd= 100 a=92 b=1 c=93
render= 9201093
dix= [9, 2, 0, 1, 0, 9, 3]
x = [9, 2, 0, 1, 0, 9]
y = [2, 0, 1, 0, 9, 3]
y = [-1, -1, -1, 0, 9, 3]
tf x = tf.Tensor([9 2 0 1 0 9], shape=(6,), dtype=int

GPT claims that 047 + 017 = 091 (gt is 064; NOPE)========
GPT claims that 034 + 055 = 091 (gt is 089; NOPE)========
GPT claims that 018 + 027 = 034 (gt is 045; NOPE)========
GPT claims that 092 + 001 = 091 (gt is 093; NOPE)========
GPT claims that 086 + 028 = 109 (gt is 114; NOPE)========
GPT claims that 086 + 030 = 111 (gt is 116; NOPE)========
GPT claims that 047 + 033 = 091 (gt is 080; NOPE)========
GPT claims that 061 + 080 = 151 (gt is 141; NOPE)========
GPT claims that 086 + 081 = 159 (gt is 167; NOPE)========
GPT claims that 032 + 002 = 051 (gt is 034; NOPE)========
GPT claims that 090 + 057 = 159 (gt is 147; NOPE)========
GPT claims that 044 + 072 = 121 (gt is 116; NOPE)========
GPT claims that 066 + 070 = 139 (gt is 136; NOPE)========
GPT claims that 071 + 035 = 109 (gt is 106; NOPE)========
GPT claims that 038 + 090 = 121 (gt is 128; NOPE)========
GPT claims that 022 + 086 = 109 (gt is 108; NOPE)========
GPT claims that 081 + 051 = 139 (gt is 132; NOPE)========
GPT claims tha

GPT claims that 033 + 085 = 111 (gt is 118; NOPE)========
GPT claims that 076 + 052 = 129 (gt is 128; NOPE)========
GPT claims that 009 + 096 = 101 (gt is 105; NOPE)========
GPT claims that 071 + 089 = 151 (gt is 160; NOPE)========
GPT claims that 027 + 022 = 051 (gt is 049; NOPE)========
GPT claims that 043 + 045 = 091 (gt is 088; NOPE)========
GPT claims that 031 + 093 = 121 (gt is 124; NOPE)========
GPT claims that 083 + 037 = 111 (gt is 120; NOPE)========
GPT claims that 066 + 016 = 091 (gt is 082; NOPE)========
GPT claims that 069 + 031 = 091 (gt is 100; NOPE)========
GPT claims that 086 + 033 = 111 (gt is 119; NOPE)========
GPT claims that 052 + 046 = 091 (gt is 098; NOPE)========
GPT claims that 055 + 064 = 121 (gt is 119; NOPE)========
GPT claims that 028 + 073 = 109 (gt is 101; NOPE)========
GPT claims that 049 + 087 = 131 (gt is 136; NOPE)========
GPT claims that 091 + 034 = 129 (gt is 125; NOPE)========
GPT claims that 001 + 037 = 051 (gt is 038; NOPE)========
GPT claims tha

GPT claims that 016 + 034 = 051 (gt is 050; NOPE)========
GPT claims that 093 + 033 = 129 (gt is 126; NOPE)========
GPT claims that 041 + 066 = 109 (gt is 107; NOPE)========
GPT claims that 093 + 047 = 151 (gt is 140; NOPE)========
GPT claims that 055 + 088 = 151 (gt is 143; NOPE)========
GPT claims that 074 + 063 = 139 (gt is 137; NOPE)========
GPT claims that 025 + 077 = 109 (gt is 102; NOPE)========
GPT claims that 024 + 091 = 111 (gt is 115; NOPE)========
GPT claims that 012 + 078 = 091 (gt is 090; NOPE)========
GPT claims that 088 + 024 = 109 (gt is 112; NOPE)========
GPT claims that 037 + 005 = 051 (gt is 042; NOPE)========
GPT claims that 055 + 024 = 091 (gt is 079; NOPE)========
GPT claims that 064 + 005 = 091 (gt is 069; NOPE)========
GPT claims that 030 + 039 = 071 (gt is 069; NOPE)========
GPT claims that 051 + 036 = 091 (gt is 087; NOPE)========
GPT claims that 085 + 039 = 111 (gt is 124; NOPE)========
GPT claims that 066 + 032 = 091 (gt is 098; NOPE)========
GPT claims tha

GPT claims that 001 + 052 = 091 (gt is 053; NOPE)========
GPT claims that 042 + 066 = 111 (gt is 108; NOPE)========
GPT claims that 049 + 051 = 101 (gt is 100; NOPE)========
GPT claims that 064 + 060 = 129 (gt is 124; NOPE)========
GPT claims that 082 + 028 = 109 (gt is 110; NOPE)========
GPT claims that 045 + 011 = 091 (gt is 056; NOPE)========
GPT claims that 080 + 054 = 139 (gt is 134; NOPE)========
GPT claims that 052 + 065 = 111 (gt is 117; NOPE)========
GPT claims that 088 + 073 = 159 (gt is 161; NOPE)========
GPT claims that 043 + 081 = 121 (gt is 124; NOPE)========
GPT claims that 080 + 076 = 159 (gt is 156; NOPE)========
GPT claims that 094 + 062 = 159 (gt is 156; NOPE)========
GPT claims that 021 + 077 = 109 (gt is 098; NOPE)========
GPT claims that 059 + 070 = 131 (gt is 129; NOPE)========
GPT claims that 086 + 063 = 151 (gt is 149; NOPE)========
GPT claims that 041 + 059 = 101 (gt is 100; NOPE)========
GPT claims that 094 + 098 = 199 (gt is 192; NOPE)========
GPT claims tha

...

GPT claims that 057 + 031 = 091 (gt is 088; NOPE)========
GPT claims that 058 + 023 = 091 (gt is 081; NOPE)========
GPT claims that 025 + 074 = 109 (gt is 099; NOPE)========
GPT claims that 059 + 021 = 091 (gt is 080; NOPE)========
GPT claims that 023 + 039 = 061 (gt is 062; NOPE)========
GPT claims that 090 + 008 = 109 (gt is 098; NOPE)========
GPT claims that 035 + 092 = 121 (gt is 127; NOPE)========
GPT claims that 016 + 060 = 091 (gt is 076; NOPE)========
GPT claims that 015 + 069 = 091 (gt is 084; NOPE)========
GPT claims that 063 + 057 = 121 (gt is 120; NOPE)========
GPT claims that 056 + 091 = 151 (gt is 147; NOPE)========
GPT claims that 055 + 081 = 131 (gt is 136; NOPE)========
GPT claims that 067 + 085 = 151 (gt is 152; NOPE)========
GPT claims that 070 + 092 = 151 (gt is 162; NOPE)========
GPT claims that 045 + 055 = 101 (gt is 100; NOPE)========
GPT claims that 072 + 047 = 111 (gt is 119; NOPE)========
GPT claims that 012 + 073 = 091 (gt is 085; NOPE)========
GPT claims tha

GPT claims that 025 + 025 = 051 (gt is 050; NOPE)========
GPT claims that 070 + 006 = 091 (gt is 076; NOPE)========
GPT claims that 063 + 013 = 091 (gt is 076; NOPE)========
GPT claims that 034 + 092 = 121 (gt is 126; NOPE)========
GPT claims that 031 + 023 = 061 (gt is 054; NOPE)========
GPT claims that 027 + 009 = 031 (gt is 036; NOPE)========
GPT claims that 049 + 068 = 111 (gt is 117; NOPE)========
GPT claims that 051 + 001 = 091 (gt is 052; NOPE)========
GPT claims that 037 + 000 = 051 (gt is 037; NOPE)========
GPT claims that 042 + 092 = 131 (gt is 134; NOPE)========
GPT claims that 048 + 071 = 121 (gt is 119; NOPE)========
GPT claims that 074 + 086 = 151 (gt is 160; NOPE)========
GPT claims that 045 + 088 = 131 (gt is 133; NOPE)========
GPT claims that 057 + 044 = 091 (gt is 101; NOPE)========
GPT claims that 037 + 047 = 091 (gt is 084; NOPE)========
GPT claims that 044 + 039 = 091 (gt is 083; NOPE)========
GPT claims that 040 + 083 = 121 (gt is 123; NOPE)========
GPT claims tha

GPT claims that 098 + 082 = 189 (gt is 180; NOPE)========
GPT claims that 055 + 074 = 131 (gt is 129; NOPE)========
GPT claims that 097 + 093 = 189 (gt is 190; NOPE)========
GPT claims that 053 + 070 = 121 (gt is 123; NOPE)========
GPT claims that 031 + 058 = 091 (gt is 089; NOPE)========
GPT claims that 019 + 074 = 091 (gt is 093; NOPE)========
GPT claims that 037 + 067 = 109 (gt is 104; NOPE)========
GPT claims that 022 + 042 = 071 (gt is 064; NOPE)========
GPT claims that 076 + 002 = 091 (gt is 078; NOPE)========
GPT claims that 061 + 098 = 151 (gt is 159; NOPE)========
GPT claims that 008 + 001 = 010 (gt is 009; NOPE)========
GPT claims that 048 + 001 = 071 (gt is 049; NOPE)========
GPT claims that 024 + 002 = 031 (gt is 026; NOPE)========
GPT claims that 055 + 022 = 091 (gt is 077; NOPE)========
GPT claims that 043 + 051 = 091 (gt is 094; NOPE)========
GPT claims that 088 + 094 = 189 (gt is 182; NOPE)========
GPT claims that 023 + 057 = 091 (gt is 080; NOPE)========
GPT claims tha

GPT claims that 027 + 001 = 031 (gt is 028; NOPE)========
GPT claims that 039 + 099 = 121 (gt is 138; NOPE)========
GPT claims that 091 + 007 = 109 (gt is 098; NOPE)========
GPT claims that 011 + 000 = 031 (gt is 011; NOPE)========
GPT claims that 057 + 077 = 131 (gt is 134; NOPE)========
GPT claims that 051 + 013 = 091 (gt is 064; NOPE)========
GPT claims that 094 + 070 = 159 (gt is 164; NOPE)========
GPT claims that 077 + 038 = 109 (gt is 115; NOPE)========
GPT claims that 077 + 004 = 091 (gt is 081; NOPE)========
GPT claims that 077 + 040 = 129 (gt is 117; NOPE)========
GPT claims that 006 + 076 = 091 (gt is 082; NOPE)========
GPT claims that 041 + 000 = 071 (gt is 041; NOPE)========
GPT claims that 012 + 027 = 034 (gt is 039; NOPE)========
GPT claims that 013 + 094 = 101 (gt is 107; NOPE)========
GPT claims that 067 + 091 = 151 (gt is 158; NOPE)========
GPT claims that 008 + 000 = 010 (gt is 008; NOPE)========
GPT claims that 025 + 060 = 091 (gt is 085; NOPE)========
GPT claims tha

GPT claims that 087 + 000 = 091 (gt is 087; NOPE)========
GPT claims that 011 + 022 = 034 (gt is 033; NOPE)========
GPT claims that 031 + 009 = 051 (gt is 040; NOPE)========
GPT claims that 008 + 099 = 101 (gt is 107; NOPE)========
GPT claims that 014 + 091 = 101 (gt is 105; NOPE)========
GPT claims that 094 + 069 = 189 (gt is 163; NOPE)========
GPT claims that 075 + 015 = 091 (gt is 090; NOPE)========
GPT claims that 088 + 013 = 099 (gt is 101; NOPE)========
GPT claims that 016 + 090 = 101 (gt is 106; NOPE)========
GPT claims that 092 + 035 = 129 (gt is 127; NOPE)========
GPT claims that 052 + 077 = 121 (gt is 129; NOPE)========
GPT claims that 013 + 052 = 091 (gt is 065; NOPE)========
GPT claims that 099 + 018 = 111 (gt is 117; NOPE)========
GPT claims that 022 + 070 = 101 (gt is 092; NOPE)========
GPT claims that 084 + 061 = 139 (gt is 145; NOPE)========
GPT claims that 084 + 049 = 139 (gt is 133; NOPE)========
GPT claims that 068 + 054 = 129 (gt is 122; NOPE)========
GPT claims tha

In [78]:
give_exam(test_dataset,batch_size=1,max_batches=-1,printResult=True)

idx=9927 nd= 100 a=99 b=27 c=126
render= 9927126
dix= [9, 9, 2, 7, 1, 2, 6]
x = [9, 9, 2, 7, 1, 2]
y = [9, 2, 7, 1, 2, 6]
y = [-1, -1, -1, 1, 2, 6]
tf x = tf.Tensor([9 9 2 7 1 2], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  2  6], shape=(6,), dtype=int32)
b=0
x=tf.Tensor([[9 9 2 7 1 2]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  1  2  6]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[9 9 2 7]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[9 9 2 7 1 1 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[1 1 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([99], shape=(1,), dtype=int32)
d2i=tf.Tensor([27], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([111], shape=(1,), dtype=int32)
GPT claims that 099 + 027 = 111 (gt is 126; NOPE)========
idx=3245 nd= 100 a=32 b=45 c=77
render= 3245077
dix= [3, 2, 4, 5, 0, 7, 7]
x = [3, 2, 4, 5, 0, 7]
y = [2, 4, 5, 0, 7, 7]
y = [-1, -1, -1, 0, 7, 7]
tf x = tf.Tensor([3 2 4 5 0 7], s

d1d2d3=tf.Tensor([[4 6 4 5 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([46], shape=(1,), dtype=int32)
d2i=tf.Tensor([45], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([91], shape=(1,), dtype=int32)
GPT claims that 046 + 045 = 091 (gt is 091; YEP!!!)
idx=8706 nd= 100 a=87 b=6 c=93
render= 8706093
dix= [8, 7, 0, 6, 0, 9, 3]
x = [8, 7, 0, 6, 0, 9]
y = [7, 0, 6, 0, 9, 3]
y = [-1, -1, -1, 0, 9, 3]
tf x = tf.Tensor([8 7 0 6 0 9], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  9  3], shape=(6,), dtype=int32)
b=14
x=tf.Tensor([[8 7 0 6 0 9]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  0  9  3]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[8 7 0 6]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[8 7 0 6 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tenso

d1d2d3=tf.Tensor([[5 4 4 6 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([54], shape=(1,), dtype=int32)
d2i=tf.Tensor([46], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([91], shape=(1,), dtype=int32)
GPT claims that 054 + 046 = 091 (gt is 100; NOPE)========
idx=5739 nd= 100 a=57 b=39 c=96
render= 5739096
dix= [5, 7, 3, 9, 0, 9, 6]
x = [5, 7, 3, 9, 0, 9]
y = [7, 3, 9, 0, 9, 6]
y = [-1, -1, -1, 0, 9, 6]
tf x = tf.Tensor([5 7 3 9 0 9], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  9  6], shape=(6,), dtype=int32)
b=29
x=tf.Tensor([[5 7 3 9 0 9]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  0  9  6]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[5 7 3 9]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[5 7 3 9 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=t

d1d2d3=tf.Tensor([[7 0 3 0 1 0 9]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[1 0 9]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([70], shape=(1,), dtype=int32)
d2i=tf.Tensor([30], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([109], shape=(1,), dtype=int32)
GPT claims that 070 + 030 = 109 (gt is 100; NOPE)========
idx=1989 nd= 100 a=19 b=89 c=108
render= 1989108
dix= [1, 9, 8, 9, 1, 0, 8]
x = [1, 9, 8, 9, 1, 0]
y = [9, 8, 9, 1, 0, 8]
y = [-1, -1, -1, 1, 0, 8]
tf x = tf.Tensor([1 9 8 9 1 0], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  0  8], shape=(6,), dtype=int32)
b=39
x=tf.Tensor([[1 9 8 9 1 0]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  1  0  8]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[1 9 8 9]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[1 9 8 9 1 0 9]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[1 0 9]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i

d1d2d3=tf.Tensor([[4 8 1 4 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([48], shape=(1,), dtype=int32)
d2i=tf.Tensor([14], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([91], shape=(1,), dtype=int32)
GPT claims that 048 + 014 = 091 (gt is 062; NOPE)========
idx=2825 nd= 100 a=28 b=25 c=53
render= 2825053
dix= [2, 8, 2, 5, 0, 5, 3]
x = [2, 8, 2, 5, 0, 5]
y = [8, 2, 5, 0, 5, 3]
y = [-1, -1, -1, 0, 5, 3]
tf x = tf.Tensor([2 8 2 5 0 5], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  5  3], shape=(6,), dtype=int32)
b=54
x=tf.Tensor([[2 8 2 5 0 5]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  0  5  3]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[2 8 2 5]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[2 8 2 5 0 5 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 5 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=t

...

d1d2d3=tf.Tensor([[5 6 7 5 1 3 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[1 3 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([56], shape=(1,), dtype=int32)
d2i=tf.Tensor([75], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([131], shape=(1,), dtype=int32)
GPT claims that 056 + 075 = 131 (gt is 131; YEP!!!)
idx=6069 nd= 100 a=60 b=69 c=129
render= 6069129
dix= [6, 0, 6, 9, 1, 2, 9]
x = [6, 0, 6, 9, 1, 2]
y = [0, 6, 9, 1, 2, 9]
y = [-1, -1, -1, 1, 2, 9]
tf x = tf.Tensor([6 0 6 9 1 2], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  2  9], shape=(6,), dtype=int32)
b=949
x=tf.Tensor([[6 0 6 9 1 2]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  1  2  9]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[6 0 6 9]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[6 0 6 9 1 3 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[1 3 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.T

d1d2d3=tf.Tensor([[1 1 6 4 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([11], shape=(1,), dtype=int32)
d2i=tf.Tensor([64], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([91], shape=(1,), dtype=int32)
GPT claims that 011 + 064 = 091 (gt is 075; NOPE)========
idx=8759 nd= 100 a=87 b=59 c=146
render= 8759146
dix= [8, 7, 5, 9, 1, 4, 6]
x = [8, 7, 5, 9, 1, 4]
y = [7, 5, 9, 1, 4, 6]
y = [-1, -1, -1, 1, 4, 6]
tf x = tf.Tensor([8 7 5 9 1 4], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  1  4  6], shape=(6,), dtype=int32)
b=964
x=tf.Tensor([[8 7 5 9 1 4]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  1  4  6]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[8 7 5 9]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[8 7 5 9 1 5 9]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[1 5 9]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i

d1d2d3=tf.Tensor([[4 5 5 7 1 0 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[1 0 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([45], shape=(1,), dtype=int32)
d2i=tf.Tensor([57], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([101], shape=(1,), dtype=int32)
GPT claims that 045 + 057 = 101 (gt is 102; NOPE)========
idx=364 nd= 100 a=3 b=64 c=67
render= 0364067
dix= [0, 3, 6, 4, 0, 6, 7]
x = [0, 3, 6, 4, 0, 6]
y = [3, 6, 4, 0, 6, 7]
y = [-1, -1, -1, 0, 6, 7]
tf x = tf.Tensor([0 3 6 4 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  7], shape=(6,), dtype=int32)
b=974
x=tf.Tensor([[0 3 6 4 0 6]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  0  6  7]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[0 3 6 4]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[0 3 6 4 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=t

d1d2d3=tf.Tensor([[9 3 0 1 0 9 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 9 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([93], shape=(1,), dtype=int32)
d2i=tf.Tensor([1], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([91], shape=(1,), dtype=int32)
GPT claims that 093 + 001 = 091 (gt is 094; NOPE)========
idx=3435 nd= 100 a=34 b=35 c=69
render= 3435069
dix= [3, 4, 3, 5, 0, 6, 9]
x = [3, 4, 3, 5, 0, 6]
y = [4, 3, 5, 0, 6, 9]
y = [-1, -1, -1, 0, 6, 9]
tf x = tf.Tensor([3 4 3 5 0 6], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  6  9], shape=(6,), dtype=int32)
b=984
x=tf.Tensor([[3 4 3 5 0 6]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  0  6  9]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[3 4 3 5]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[3 4 3 5 0 7 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 7 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=t

d1d2d3=tf.Tensor([[3 9 0 0 0 5 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 5 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=tf.Tensor([39], shape=(1,), dtype=int32)
d2i=tf.Tensor([0], shape=(1,), dtype=int32)
d3i_pred=tf.Tensor([51], shape=(1,), dtype=int32)
GPT claims that 039 + 000 = 051 (gt is 039; NOPE)========
idx=3613 nd= 100 a=36 b=13 c=49
render= 3613049
dix= [3, 6, 1, 3, 0, 4, 9]
x = [3, 6, 1, 3, 0, 4]
y = [6, 1, 3, 0, 4, 9]
y = [-1, -1, -1, 0, 4, 9]
tf x = tf.Tensor([3 6 1 3 0 4], shape=(6,), dtype=int32)
tf y = tf.Tensor([-1 -1 -1  0  4  9], shape=(6,), dtype=int32)
b=994
x=tf.Tensor([[3 6 1 3 0 4]], shape=(1, 6), dtype=int32)
y=tf.Tensor([[-1 -1 -1  0  4  9]], shape=(1, 6), dtype=int32)
d1d2=tf.Tensor([[3 6 1 3]], shape=(1, 4), dtype=int32)
d1d2d3=tf.Tensor([[3 6 1 3 0 6 1]], shape=(1, 7), dtype=int32)
d3=tf.Tensor([[0 6 1]], shape=(1, 3), dtype=int32)
factors=tf.Tensor([[100  10   1]], shape=(1, 3), dtype=int32)
d1i=t